Disable autoscroll

In [1]:
%%javascript
IPython.OutputArea.prototype._should_scroll = function(lines) {
    return false;
}

<IPython.core.display.Javascript object>

In [173]:
import pandas as pd
import numpy as np
import pathlib
import os
import pandas_profiling as pp

In [208]:
#load metadata and fulltext

meta_path = pathlib.Path.cwd().parent.parent / 'datasets' / 'metadata.pckl.gz'
full_path = pathlib.Path.cwd().parent.parent / 'datasets' / 'fulltext.pckl.gz'

metadata = pd.read_pickle(meta_path, compression='gzip')
fulltext = pd.read_pickle(full_path, compression='gzip')

In [209]:
# replace 'Null' with NaN
fulltext.replace(to_replace='Null', value=np.nan, inplace=True)
metadata.replace(to_replace='Null', value=np.nan, inplace=True)

In [210]:
# uncomment to view profiling report
pp.ProfileReport(metadata)

In [211]:
# uncomment to view profiling report
pp.ProfileReport(fulltext)

In [7]:
# see non-empty entries in corrections column
[x for x in metadata.corrections.values if len(x)>0]

[['https://www.federalregister.gov/api/v1/documents/C1-2013-10220']]

In [8]:
#see non-empty entry in corrections_of column
metadata.json_url[metadata.correction_of.isnull()==False].values

array(['https://www.federalregister.gov/api/v1/documents/C1-2013-10220?publication_date=2013-05-07'],
      dtype=object)

The only non-empty entry in each of these two columns refers to the same singular linkage.

In [153]:
# already completed
# check values of action column
# metadata.action.value_counts()

Note: the above has already been corrected. The original version contained 3 variations on "Notice" and 9 variations on "Correction" : 

Notice.                          2857
Notice; correction.              215 
Notice                           185 
Correction.                      7   
Notice; request for comments.    3   
Correction                       2   
Notice; correction               2   
Notice: Correction.              1   
Notice..                         1   
Notice; Correction.              1   
Notice, correction.              1   
Name: action, dtype: int64


In [95]:
# already completed

#correct variations of 'notice' to most popular version

# notice_variations = ['Notice', 'Notice..']
# for x in notice_variations:
#     metadata.action.replace(to_replace=x, value='Notice.', inplace=True)

In [154]:
# already completed

#check new action values
# metadata.action.value_counts()

Original output: 

Notice.                          3043
Notice; correction.              215 
Correction.                      7   
Notice; request for comments.    3   
Correction                       2   
Notice; correction               2   
Notice: Correction.              1   
Notice; Correction.              1   
Notice, correction.              1   
Name: action, dtype: int64

In [155]:
# already completed

#correct variations of 'correction' to most popular version
# correction_variations = ['Correction.', 'Notice; correction', 'Correction', 
#                          'Notice, correction.', 'Correction', 'Notice, correction.', 
#                          'Notice; Correction.', 'Notice: Correction.']
# for x in correction_variations:
#     metadata.action.replace(to_replace=x, value='Notice; correction.', inplace=True)

In [98]:
#check new action values
metadata.action.value_counts()

Notice.                          3043
Notice; correction.              229 
Notice; request for comments.    3   
Name: action, dtype: int64

In [99]:
#save changes to pickle
# metadata.to_pickle(meta_path, compression='gzip')

## Investigate Recycled Text

In [11]:
summary_multiples = [x for x in fulltext.summary.value_counts() if x>1]

In [13]:
len(summary_multiples)

150

In [213]:
np.sum(summary_multiples)

482

In [100]:
summary_multiples[:20]

[18, 11, 10, 9, 9, 8, 8, 7, 7, 7, 7, 7, 7, 6, 6, 6, 6, 6, 5, 5]

In [101]:
pd.set_option('display.max_colwidth', -1)
# view top 7
# this is all values with 8 or more repeats
summary_repeats = pd.DataFrame(data = {'Fulltext Summary': fulltext.summary.value_counts()[:7].index,
                                       'Number of Repeats': summary_multiples[:7]})
summary_repeats.set_index('Number of Repeats', inplace=True)
summary_repeats

Fulltext Summary
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
18                 The State Historical Society of Wisconsin has completed an inventory of human remains, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and any present-day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request to the State Historical Society of Wisconsin. If no additional requestors come forward, transfer of control of the human remains to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                                                                                                                        
11                 The Wisconsin Historical Society has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian Tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian Tribes or Native Hawaiian organizations. Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the Wisconsin Historical Society. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian Tribes or Native Hawaiian organizations stated in this notice may proceed.                                                          
10                 The University of Michigan has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the University of Michigan. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                      
9                  The Minnesota Indian Affairs Council has completed an inventory of human remains in consultation with the appropriate Indian tribes, and has determined that there is no cultural affiliation between the remains and any present-day Indian tribe. Representatives of any Indian tr

In [102]:
abstract_multiples = [x for x in metadata.abstract.value_counts() if x>1]

In [103]:
len(abstract_multiples)

149

In [214]:
np.sum(abstract_multiples)

481

In [104]:
abstract_multiples[:20]

[18, 11, 10, 9, 9, 8, 8, 7, 7, 7, 7, 7, 7, 6, 6, 6, 6, 6, 5, 5]

Seeing a similar pattern as in fulltext summary!

In [105]:
# view top 7
# this is all values with 9 or more repeats

abstract_repeats = pd.DataFrame(data = {'Metadata Abstract': metadata.abstract.value_counts()[:7].index,
                                       'Number of Repeats': abstract_multiples[:7]})
abstract_repeats.set_index('Number of Repeats', inplace=True)
abstract_repeats

Metadata Abstract
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
18                 The State Historical Society of Wisconsin has completed an inventory of human remains, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and any present- day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request to the State Historical Society of Wisconsin. If no additional requestors come forward, transfer of control of the human remains to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                                                                                                                       
11                 The Wisconsin Historical Society has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian Tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian Tribes or Native Hawaiian organizations. Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the Wisconsin Historical Society. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian Tribes or Native Hawaiian organizations stated in this notice may proceed.                                                          
10                 The University of Michigan has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the University of Michigan. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                      
9                  The Minnesota Indian Affairs Council has completed an inventory of human remains in consultation with the appropriate Indian tribes, and has determined that there is no cultural affiliation between the remains and any present-day Indian tribe. Representatives of any Indian t

In [106]:
consultation_multiples = [x for x in fulltext.consultation.value_counts() if x>1]
len(consultation_multiples)

58

In [215]:
np.sum(consultation_multiples)

176

In [107]:
consultation_multiples[:20]

[25, 9, 6, 5, 4, 4, 4, 4, 4, 4, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3]

In [108]:
# view top 10
# this is all values with 4 or more repeats
consultation_repeats = pd.DataFrame(data = {'Fulltext Consultation': fulltext.consultation.value_counts()[:10].index,
                                       'Number of Repeats': consultation_multiples[:10]})
consultation_repeats.set_index('Number of Repeats', inplace=True)
consultation_repeats

Fulltext Consultation
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                     
25                 A detailed assessment of the human remains was made by the State Historical Society of Wisconsin professional staff in consultation with representatives of the Forest County Potawatomi Community, Wisconsin; Ho-Chunk Nation of Wisconsin; and the Menominee Indian Tribe of Wisconsin. \n                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                    

In [109]:
determinations_multiples = [x for x in fulltext.determinations.value_counts() if x>1]
len(determinations_multiples)

7

In [216]:
np.sum(determinations_multiples)

16

In [110]:
# view top 7
# this is all values with 2 or more repeats
fulltext.determinations.value_counts()[:7]

determinations_repeats = pd.DataFrame(data = {'Fulltext Determinations': fulltext.determinations.value_counts()[:7].index,
                                       'Number of Repeats': determinations_multiples[:7]})
determinations_repeats.set_index('Number of Repeats', inplace=True)
determinations_repeats

Fulltext Determinations
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
4                  Determinations Made by History Colorado \n Officials of History Colorado have determined that: \n \xe2\x80\xa2 Based on osteological analysis, the human remains are Native American. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(9), the human remains described in this notice represent the physical remains of one individual of Native American ancestry. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(2), a relationship of shared group identity cannot be reasonably traced between the Native American human remains and any present-day Indian tribe. \n \xe2\x80\xa2 Pursuant to 43 CFR 10.11(c)(2)(ii) and the Process, the disposition of the human remains may be to the Southern Ute Indian Tribe of the Southern Ute Reservation, Colorado, and the Ute Mountain Tribe of the Ute Mountain Reservation, Colorado, New Mexico & Utah. \n                                                                                                                                                                                                                                                                                                                                                                                                  
2                  Determinations Made by History Colorado \n Officials of History Colorado have determined that: \n \xe2\x80\xa2 Based on osteological analysis, the human remains are Native American. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(9), the human remains described in this notice represent the physical remains of seven individuals of Native American ancestry. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(2), a relationship of shared group identity cannot be reasonably traced between the Native American human remains and any present-day Indian tribe. \n \xe2\x80\xa2 Pursuant to 43 CFR 10.11(c)(2)(ii) and the Process, the disposition of the human remains may be to the Southern Ute Indian Tribe of the Southern Ute Reservation, Colorado, and the Ute Mountain Tribe of the Ute Mountain Reservation, Colorado, New Mexico & Utah. \n                                                                                                                                                                                                                                                                                                                                                                                               
2                  Determinations Made by the Department of Anthropology at Indiana University \n Officials of the Department of Anthropology at Indiana University have determined that: \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(9), the human remains described in this notice represent the physical

In [111]:
ard_multiples = [x for x in fulltext.a_r_d.value_counts() if x>1]
len(ard_multiples)

44

In [217]:
np.sum(ard_multiples)

125

In [112]:
ard_multiples[:20]

[8, 7, 7, 6, 5, 4, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 3, 2, 2]

In [207]:
# view top 6
# this is all values with 4 or more repeats
ard_repeats = pd.DataFrame(data = {'Fulltext Additional Requestors and Disposition': fulltext.a_r_d.value_counts()[:6].index,
                                       'Number of Repeats': ard_multiples[:6]})
ard_repeats.set_index('Number of Repeats', inplace=True)
ard_repeats

Fulltext Additional Requestors and Disposition
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                 
8                  Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to Jennifer Kolb, Wisconsin Historical Museum, 30 North Carroll Street, Madison, WI 53703, telephone (608) 261-2461, email Jennifer.Kolb@wisconsinhistory.org, by October 10, 2014. After that date, if no additional requestors have come forward, transfer of control of the human remains to The Aboriginal Land Tribes may proceed. \n The State Historical Society of Wisconsin is responsible for notifying The Aboriginal Land Tribes that this notice has been published. \n                                                                                              
7                  Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of the request to Dr. Ben Secunda, NAGPRA Project Manager, University of Michigan, Office of the Vice President for Research, 4080 Fleming Building, 503 Thompson St., Ann Arbor, MI 48109-1340, telephone (734) 647-9085, email bsecunda@umich.edu, by December 2, 2013. After that date, if no additional requestors have come forward, transfer of control of the human remains and associated funerary objects to The Tribes may proceed. \n The University of Michigan is responsible for notifying The Tribes that this notice has been published. \n      
7                  Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to Patricia Capone, Museum Curator and Director of Research and Repatriation, Peabody Museum of Archaeology and Ethnology, Harvard University, 11 Divinity Avenue, Cambridge, MA 02138, telephone (617) 496-3702, email pcapone@fas.harvard.edu by November 2, 2016. After that date, if no additional requestors have come forward, transfer of control of the human remains to The Aboriginal Land Tribes may proceed. \n The Peabody Museum of Archaeology and Ethnology is responsible for notifying The Invited and Consulted Tribes that this notice has been published. \n 
6                  Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to Jeffrey Sommer, Historical Society of Saginaw County, Inc., 500 Federal Avenue, Saginaw, MI 48607, telephone (989) 752-2861 Ext. 308, email jsommer@castlemuseum.org, by April 17, 2019. After that date, if no additional requestors have come forward, transfer of control of the human remains to The Consulted and Invited Tribes may proceed. \n The Historical Society of Saginaw County, Inc. is responsible for notifying 

In [114]:
date_multiples_full = [x for x in fulltext.dates.value_counts() if x>1]
len(date_multiples_full)

134

In [218]:
np.sum(date_multiples_full)

382

In [115]:
date_multiples_meta = [x for x in metadata.dates.value_counts() if x>1]
len(date_multiples_meta)

181

In [219]:
np.sum(date_multiples_meta)

968

In [116]:
date_multiples_full[:20]

[11, 9, 8, 7, 6, 6, 6, 6, 6, 6, 5, 5, 5, 5, 4, 4, 4, 4, 4, 4]

In [117]:
date_multiples_meta[:20]

[75, 61, 55, 51, 43, 38, 29, 27, 20, 19, 15, 14, 9, 9, 9, 9, 9, 8, 8, 8]

Dates are reused much more often in metadata than in fulltext.

In [118]:
# view top 10
# this is all values with 6 or more repeats
full_dates_repeats = pd.DataFrame(data = {'Fulltext Dates': fulltext.dates.value_counts()[:10].index,
                                       'Number of Repeats': date_multiples_full[:10]})
full_dates_repeats.set_index('Number of Repeats', inplace=True)
full_dates_repeats

Fulltext Dates
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                
11                 Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the State Historical Society of Wisconsin at the address in this notice by October 10, 2014.                                                  
9                  Lineal descendants or representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to Texas A&M University at the address in this notice by May 19, 2014.                                                     
8                  Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the Peabody Museum of Archaeology and Ethnology at the address in this notice by November 2, 2016.                                            
7                  Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of the request to the University of Wisconsin-Madison Department of Anthropology at the address in this notice by June 16, 2014.
6                  Representatives of any Indian Tribe that believes it has a cultural affiliation with the human remains should contact the museum at the address below by March 21, 2011.                                                                                                                                                                                                                      
6                  Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of the request to the Wisconsin Historical Society at the address in this notice by May 21, 2018.                               
6                  Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of the request to the University of Michigan at the address in this notice by December 2, 2013.                                 
6                  Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the Peabody Museum of Archaeology and Ethnology at the address in this notice by January 22, 2019.                                            
6                  Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the Historical Society of Saginaw County, Inc. at the address in this notice by April 17, 2019.             

In [119]:
# view top 10
# this is all values with 15 or more repeats
metadata.dates.value_counts()[:10]

meta_dates_repeats = pd.DataFrame(data = {'Metadata Dates': metadata.dates.value_counts()[:10].index,
                                       'Number of Repeats': date_multiples_meta[:10]})
meta_dates_repeats.set_index('Number of Repeats', inplace=True)
meta_dates_repeats

Metadata Dates
Number of Repeats                                                                                                                                                                                                                                                                             
75                 Lineal descendants or representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in
61                 Lineal descendants or representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in
55                 Lineal descendants or representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the  
51                 Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of           
43                 Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of           
38                 Lineal descendants or representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the  
29                 Representatives of any Indian tribe that believes it has a cultural affiliation with the human remains should contact the                                                                                                                                                  
27                 Representatives of any Indian tribe that believes it has a cultural affiliation with the human remains and associated funerary                                                                                                                                             
20                 Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the State                  
19                 Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the University of

In [120]:
summary_repeats # merge with below
abstract_repeats # merge with above
consultation_repeats
determinations_repeats # some cut off
ard_repeats
full_dates_repeats
meta_dates_repeats # cut off

Metadata Dates
Number of Repeats                                                                                                                                                                                                                                                                             
75                 Lineal descendants or representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in
61                 Lineal descendants or representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in
55                 Lineal descendants or representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the  
51                 Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of           
43                 Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request with information in support of           
38                 Lineal descendants or representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the  
29                 Representatives of any Indian tribe that believes it has a cultural affiliation with the human remains should contact the                                                                                                                                                  
27                 Representatives of any Indian tribe that believes it has a cultural affiliation with the human remains and associated funerary                                                                                                                                             
20                 Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the State                  
19                 Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request with information in support of the request to the University of

### Investigate relationship between fulltext summary and metadata abstract

In [148]:
summary_and_abstract = pd.concat([summary_repeats, abstract_repeats], axis =1, ignore_index=False)

identical = summary_and_abstract['Fulltext Summary'] == summary_and_abstract['Metadata Abstract']
summary_and_abstract['Identical?'] = identical
summary_and_abstract

Fulltext Summary  \
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                           
18                 The State Historical Society of Wisconsin has completed an inventory of human remains, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and any present-day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request to the State Historical Society of Wisconsin. If no additional requestors come forward, transfer of control of the human remains to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                                                                                                                           
11                 The Wisconsin Historical Society has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian Tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian Tribes or Native Hawaiian organizations. Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the Wisconsin Historical Society. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian Tribes or Native Hawaiian organizations stated in this notice may proceed.                                                             
10                 The University of Michigan has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the University of Michigan. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                         
9                  The Minnesota Indian Affairs Council has completed an inventory of human remains in consultation with the appropriate Indian tribes, and has determined that there is no cultural affiliation between the remains and any present-day Indian tribe. Representatives o

Even the singular "False" looks identical upon human reading.

In [150]:
summary_and_abstract['Fulltext Summary / Metadata Abstract'] = summary_and_abstract['Fulltext Summary']
summary_and_abstract.drop(columns=['Fulltext Summary', 'Metadata Abstract', 'Identical?'], inplace=True)
summary_and_abstract

Fulltext Summary / Metadata Abstract
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
18                 The State Historical Society of Wisconsin has completed an inventory of human remains, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and any present-day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains should submit a written request to the State Historical Society of Wisconsin. If no additional requestors come forward, transfer of control of the human remains to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                                                                                                                        
11                 The Wisconsin Historical Society has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian Tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian Tribes or Native Hawaiian organizations. Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the Wisconsin Historical Society. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian Tribes or Native Hawaiian organizations stated in this notice may proceed.                                                          
10                 The University of Michigan has completed an inventory of human remains and associated funerary objects, in consultation with the appropriate Indian tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian tribes or Native Hawaiian organizations. Representatives of any Indian tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects should submit a written request to the University of Michigan. If no additional requestors come forward, transfer of control of the human remains and associated funerary objects to the Indian tribes or Native Hawaiian organizations stated in this notice may proceed.                                                                      
9                  The Minnesota Indian Affairs Council has completed an inventory of human remains in consultation with the appropriate Indian tribes, and has determined that there is no cultural affiliation between the remains and any present-day Indian tribe. Representati

### Investigate cut-off determinations

In [206]:
pd.set_option('display.max_colwidth', -1)

determinations_repeats

Fulltext Determinations
Number of Repeats                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                        
4                  Determinations Made by History Colorado \n Officials of History Colorado have determined that: \n \xe2\x80\xa2 Based on osteological analysis, the human remains are Native American. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(9), the human remains described in this notice represent the physical remains of one individual of Native American ancestry. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(2), a relationship of shared group identity cannot be reasonably traced between the Native American human remains and any present-day Indian tribe. \n \xe2\x80\xa2 Pursuant to 43 CFR 10.11(c)(2)(ii) and the Process, the disposition of the human remains may be to the Southern Ute Indian Tribe of the Southern Ute Reservation, Colorado, and the Ute Mountain Tribe of the Ute Mountain Reservation, Colorado, New Mexico & Utah. \n                                                                                                                                                                                                                                                                                                                                                                                                  
2                  Determinations Made by History Colorado \n Officials of History Colorado have determined that: \n \xe2\x80\xa2 Based on osteological analysis, the human remains are Native American. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(9), the human remains described in this notice represent the physical remains of seven individuals of Native American ancestry. \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(2), a relationship of shared group identity cannot be reasonably traced between the Native American human remains and any present-day Indian tribe. \n \xe2\x80\xa2 Pursuant to 43 CFR 10.11(c)(2)(ii) and the Process, the disposition of the human remains may be to the Southern Ute Indian Tribe of the Southern Ute Reservation, Colorado, and the Ute Mountain Tribe of the Ute Mountain Reservation, Colorado, New Mexico & Utah. \n                                                                                                                                                                                                                                                                                                                                                                                               
2                  Determinations Made by the Department of Anthropology at Indiana University \n Officials of the Department of Anthropology at Indiana University have determined that: \n \xe2\x80\xa2 Pursuant to 25 U.S.C. 3001(9), the human remains described in this notice represent the physical

In [161]:
cutoff_1 = determinations_repeats.iloc[-1]['Fulltext Determinations']
cutoff_2 = determinations_repeats.iloc[4]['Fulltext Determinations']

In [168]:
pd.reset_option('display.max_colwidth')
fulltext[fulltext['determinations']==cutoff_1]['supp_info'].values

array(["SUPPLEMENTARY INFORMATION: \n Notice is here given in accordance with the Native American Graves Protection and Repatriation Act (NAGPRA), 25 U.S.C. 3003, of the completion of an inventory of human remains and associated funerary objects under the control of TVA, Knoxville, TN. The human remains and associated funerary objects were removed from archeological sites in Colbert and Lauderdale Counties, AL, and Hardin County, TN. \n This notice is published as part of the National Park Service\\'s administrative responsibilities under NAGPRA, 25 U.S.C. 3003(d)(3) and 43 CFR 10.11(d). The determinations in this notice are the sole responsibility of the museum, institution, or Federal agency that has control of the Native American human remains and associated funerary objects. The National Park Service is not responsible for the determinations in this notice. \n Consultation \n A detailed assessment of the human remains and associated funerary objects was made by TVA professional sta

In [169]:
pd.reset_option('display.max_colwidth')
fulltext[fulltext['determinations']==cutoff_2]['supp_info'].values

array(["SUPPLEMENTARY INFORMATION: \n Notice is here given in accordance with the Native American Graves Protection and Repatriation Act (NAGPRA), 25 U.S.C. 3003, of the completion of an inventory of human remains and associated funerary objects under the control of the University of Tennessee, Department of Anthropology, Knoxville, TN. The human remains and associated funerary objects were removed from Site 40MU260, the Brown site, in Maury County, TN. \n This notice is published as part of the National Park Service\\'s administrative responsibilities under NAGPRA, 25 U.S.C. 3003(d)(3) and 43 CFR 10.11(d). The determinations in this notice are the sole responsibility of the museum, institution, or Federal agency that has control of the Native American human remains and associated funerary objects. The National Park Service is not responsible for the determinations in this notice. \n Consultation \n A detailed assessment of the human remains was made by the University of Tennessee, Dep

We see that the determinations are truly cut-off. Let's get the links to the actual notices.

In [170]:
fulltext[fulltext['determinations']==cutoff_1].index

Index(['I_180', 'I_177'], dtype='object', name='index')

In [171]:
fulltext[fulltext['determinations']==cutoff_2].index

Index(['I_169', 'I_167'], dtype='object', name='index')

All the repeated cut-offs are from notices of inventory completions.

In [177]:
inv_path = pathlib.Path.cwd().parent.parent / 'datasets' / 'inv_urls.csv'

inv_urls = pd.read_csv(inv_path)

In [186]:
all_keys = list(fulltext[fulltext['determinations']==cutoff_1].index.values)+ list(fulltext[fulltext['determinations']==cutoff_2].index.values)
all_keys

['I_180', 'I_177', 'I_169', 'I_167']

In [201]:
inv_urls[inv_urls.key.isin(all_keys)]['Link'].values

array(['https://www.federalregister.gov/documents/2018/12/21/2018-27648/notice-of-inventory-completion-the-university-of-tennessee-department-of-anthropology-knoxville-tn',
       'https://www.federalregister.gov/documents/2018/12/21/2018-27646/notice-of-inventory-completion-the-university-of-tennessee-department-of-anthropology-knoxville-tn',
       'https://www.federalregister.gov/documents/2018/12/21/2018-27708/notice-of-inventory-completion-tennessee-valley-authority-knoxville-tn',
       'https://www.federalregister.gov/documents/2018/12/21/2018-27647/notice-of-inventory-completion-tennessee-valley-authority-knoxville-tn'],
      dtype=object)

In [204]:
fulltext.loc['I_180']['messy_full']

"\\n      \\n        DEPARTMENT OF THE INTERIOR\\n        National Park Service\\n        [NPS-WASO-NAGPRA-NPS0027073: PPWOCRADN0-PCU00RP14.R50000]\\n        Notice of Inventory Completion: Tennessee Valley Authority, Knoxville, TN\\n        \\n          AGENCY:\\n          National Park Service, Interior.\\n        \\n        \\n          ACTION:\\n          Notice.\\n        \\n        \\n          SUMMARY:\\n          The Tennessee Valley Authority (TVA) has completed an inventory of human remains and associated funerary objects in consultation with the appropriate Indian Tribes or Native Hawaiian organizations, and has determined that there is no cultural affiliation between the human remains and associated funerary objects and any present-day Indian Tribes or Native Hawaiian organizations. Representatives of any Indian Tribe or Native Hawaiian organization not identified in this notice that wish to request transfer of control of these human remains and associated funerary objects 

We find that the text of the determinations has made it into messy_full, but not into supp_info or determinations.